In [1]:
from collections import Counter

import altair as alt
import pandas as pd

### `Compensation` data

In [2]:
df = pd.read_csv("../data/out/lc_info.csv", na_filter=False)
df.shape

(1940, 6)

In [3]:
df["lpa"] = df["salary"] / 1_00_000
df["Years of Experience (bucket)"] = pd.cut(df["yoe"], bins=[-0.1, 1, 3, 6, 9, 15, 100],
                              labels=["0-1", "1-3", "3-6", "6-9", "9-15", "15+"])
df.rename(columns={"yoe": "Years of Experience"}, inplace=True)

In [4]:
df["company"] = df["company"].str.upper()
df["title"] = df["title"].str.upper()

In [5]:
df

company                  title   location   salary  \
0                           TCS       SYSTEMS ENGINEER  bangalore   330000   
1                        AIRTEL                  SDE 1      delhi  1200000   
2     L & T TECHNOLOGY SERVICES                  SDE 1  bangalore  1300000   
3                       INFOSYS  SPECIALIST PROGRAMMER        n/a   800000   
4                      QUALCOMM                  SDE 2  bangalore  2100000   
...                         ...                    ...        ...      ...   
1935                        N/A                  SDE 2  bangalore  3000000   
1936                     AMAZON                  SDE 1  bangalore  1600000   
1937               RELIANCE JIO                    N/A  bangalore  1560000   
1938               RELIANCE JIO                  SDE 2      delhi  2200000   
1939         PHOTON INTERACTIVE                  SDE 1  bangalore  1900000   

      Years of Experience                                      original_text  \
0                     0.0  education:btech from tier-3 college\nyears of ...   
1                     0.0  education: b.tech (cse) from tier 1 college\ny...   
2                     0.0  education: b.tech in computer engineering in t...   
3                     0.0  • education: b.tech in computer science\n• yea...   
4                     2.4  education : mtech cse from iit (2018 passout)\...   
...                   ...                                                ...   
1935                  3.0  education: b.tech. from a tier 3 university in...   
1936                  2.0  education: be cs (tier 3 college)\nyears of ex...   
1937                  6.0  education: b.tech in computer science from tie...   
1938                  4.0  education: b.tech from a tier 3 college\nyears...   
1939                  2.5  education: tier 1 (new iit)\nyears of experien...   

       lpa Years of Experience (bucket)  
0      3.3                          0-1  
1     12.0                          0-1  
2     13.0                          0-1  
3      8.0                          0-1  
4     21.0                          1-3  
...    ...                          ...  
1935  30.0                          1-3  
1936  16.0                          1-3  
1937  15.6                          3-6  
1938  22.0                          3-6  
1939  19.0                          1-3  

[1940 rows x 8 columns]

### Notes
- All the fields have been standardized
- Company, title and location have been using files present at `data/mappings`
- All the fields have been parsed using regex and few heuristics
- Data is for India only atm(parsing salaries is tricky)
- `salary` = fixed salary mentioned in the text(total salary is WIP)

### `Fixed Salary` distribution

In [6]:
import numpy as np

In [7]:
p75, p95, p99 = np.percentile(df["lpa"], 75), np.percentile(df["lpa"], 95), np.percentile(df["lpa"], 99)
p75, p95, p99

(27.0, 38.0, 50.0)

In [8]:
pdf = pd.DataFrame({'p75': [p75], 'p95': [p95], 'p99': [p99]})

In [9]:
bar = alt.Chart(df).mark_bar(size=23).encode(
    x=alt.X('lpa', bin=alt.Bin(maxbins=35), title="₹ LPA"),
    y=alt.Y('count()', axis=alt.Axis(title="Count")),
    color=alt.value('mediumseagreen')
).properties(width=900, height=350)

rule1 = alt.Chart(pdf).mark_rule(color='black', strokeDash=[2, 2], size=1.5).encode(
    x="p75:Q"
)
rule2 = alt.Chart(pdf).mark_rule(color='grey', strokeDash=[2, 2]).encode(
    x="p95:Q",
)
rule3 = alt.Chart(pdf).mark_rule(color='grey', strokeDash=[2, 2]).encode(
    x="p99:Q",
)

(bar + rule1 + rule2 + rule3)

alt.LayerChart(...)

### Companies with most reports

In [10]:
comp_counter = Counter(df["company"])
top_companies = [comp[0] for comp in comp_counter.most_common(31) if comp[0] != "N/A"]

In [11]:
alt.Chart(df[df.company.isin(top_companies)]).mark_bar(size=25).encode(
    x=alt.X('company', sort='-y', axis=alt.Axis(title=None)),
    y=alt.Y('count()', axis=alt.Axis(title="Count")),
    color=alt.value('mediumseagreen')
).properties(width=900, height=350)

alt.Chart(...)

In [12]:
bar = alt.Chart(df[df["company"].isin(top_companies)]).mark_circle(size=50).encode(
    x=alt.X('lpa', axis=alt.Axis(title="₹ LPA")),
    y=alt.Y('company', axis=alt.Axis(title=None),
            sort=alt.EncodingSortField(field="lpa", op="mean", order='descending')),
    color=alt.Color('company', legend=None)
).properties(width=850, height=800)

rule1 = alt.Chart(pdf).mark_rule(color='black', strokeDash=[2, 2], size=1.5).encode(
    x="p75:Q"
)
rule2 = alt.Chart(pdf).mark_rule(color='grey', strokeDash=[2, 2]).encode(
    x="p95:Q",
)
rule3 = alt.Chart(pdf).mark_rule(color='grey', strokeDash=[2, 2]).encode(
    x="p99:Q",
)

bar + rule1 + rule2 + rule3

alt.LayerChart(...)

### Salary by `title`

In [13]:
title_counter = Counter(df["title"])
top_titles = [title[0] for title in title_counter.most_common(21) if title[0] != "N/A"]

bar = alt.Chart(df[df["title"].isin(top_titles)]).mark_boxplot(size=25, color="grey").encode(
    x=alt.X('lpa', title="₹ LPA"),
    y=alt.Y('title', axis=alt.Axis(title=None)),
    color=alt.Color('title', legend=None)
).properties(width=800, height=600)

rule1 = alt.Chart(pdf).mark_rule(color='black', strokeDash=[2, 2], size=1.5).encode(
    x="p75:Q"
)
rule2 = alt.Chart(pdf).mark_rule(color='grey', strokeDash=[2, 2]).encode(
    x="p95:Q",
)
rule3 = alt.Chart(pdf).mark_rule(color='grey', strokeDash=[2, 2]).encode(
    x="p99:Q",
)

(bar + rule1 + rule2 + rule3).configure_point(size=8)

alt.LayerChart(...)

### Salary by `experience`

In [14]:
alt.Chart(df[(df["Years of Experience"]!=-1)]).mark_point(color="black", size=10).encode(
    x='Years of Experience',
    y=alt.Y('lpa', title="₹ LPA"),
    color=alt.condition('datum.company=="AMAZON"', alt.ColorValue('orange'), alt.ColorValue('black'))
).properties(width=800, height=600)

alt.Chart(...)

In [15]:
alt.Chart(df[(df["Years of Experience"]!=-1)&(df['Years of Experience (bucket)']!="15+")]).mark_boxplot(color="grey", size=40).encode(
    x='Years of Experience (bucket)',
    y=alt.Y('lpa', title="₹ LPA"),
    color=alt.value('mediumseagreen')
).properties(width=800, height=500)

alt.Chart(...)

In [16]:
top_c = ['GOOGLE', 'AMAZON', 'MICROSOFT', 'UBER']

In [17]:
alt.Chart(df[(df["Years of Experience"]!=-1)&
             (df['company'].isin(top_c))&
             (df['Years of Experience (bucket)']!="15+")])\
.mark_boxplot(color="grey", size=10).encode(
    x=alt.X('company', title=None),
    y=alt.Y('lpa', title="₹ LPA"),
    color='company',
    column=alt.Column('Years of Experience (bucket)')
).properties(width=150, height=500)

alt.Chart(...)

### Top offers

In [18]:
print("| Company | Title | YOE | Salary | Location | Original Post")
print("| --- | --- | --- | --- | --- | --- |")
for r in df.sort_values(by="lpa", ascending=False)[:10].iterrows():
    r = r[1]
    comp, title, yoe, salary, location, txt = \
        r["company"], r["title"], r["Years of Experience"], r["salary"], r["location"], r["original_text"]
    print("| " + " | ".join(['`'+str(comp)+'`', title, str(yoe), "₹ " + str(salary), location, repr(txt)]) + " |")

| Company | Title | YOE | Salary | Location | Original Post
| --- | --- | --- | --- | --- | --- |
| `ORACLE` | N/A | 6.0 | ₹ 7000000 | hyderabad | "education: b. tech in cse\nyears of experience: 6\nprior experience: sde 3 @ top 4 firm\ndate of the offer: q1 2021\ncompany: oracle\ntitle/level: pmts - ic4\nlocation: hyderabad, india inr\nsalary: 70,00,000 inr\nrelocation/signing bonus: 24,00,000 inr (signing bonus)\nstock bonus: 2500 units = $45k per yr for 4 years\nbonus: n/a\ntotal comp (salary + bonus + stock): 102l inr\nbenefits: standard oracle benefits\nother details: current tc is ~90l\nwould like to hear the thoughts of the community on this.\ni know it looks like a good offer, but think from 2 perspectives -\nthere is not a huge bump being offered over my current comp\ni am concerned about oci. i've worked with only the top 4 firms so far so also worried that this might be a step down on my profile.\nlol downvoters, can you explain why you are downvoting the post? what can op d